In [3]:
import pandas as pd

the binding affinities are **only** present in the 2013 snapshot, not in the updated ones

In [48]:
df = pd.read_table('biolip/data/BioLiP_2013-03-6_nr.txt',sep='\t',header=None,usecols=[0,4,5,6,13,14,15,16,19])
df = df.rename(columns={0:'pdb',4:'chain',5:'l_id',6:'l_chain',
                        13: 'affinity_lit',14: 'affinity_moad',15: 'affinity_pdbbind-cn',16:'affinity_bindingdb',
                        19: 'seq'})

In [49]:
base = 'biolip/data/ligand/'
df['ligand_fn'] = base + df['pdb']+'_'+df['chain']+'_'+df['l_id'].astype(str)+'_'+df['l_chain'].astype(str)+'.pdb'

In [50]:
df_complex = pd.read_parquet('data/biolip_complex.parquet')

In [51]:
df_affinity = df_complex[~df_complex['affinity_lit'].isnull() | ~df_complex['affinity_moad'].isnull() 
                         | ~df_complex['affinity_pdbbind-cn'].isnull() | ~df_complex['affinity_bindingdb'].isnull()].copy()

In [57]:
from pint import UnitRegistry
import numpy as np
import re
ureg = UnitRegistry()

quantities = ['ki','kd','ka','k1/2','kb','ic50','ec50','km']

others = set()
def to_uM(affinities):
    lit, moad, pdbbind, bindingdb = affinities

    vals = []
    try:
        q = re.split('[=~<>]',str(lit))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(lit))[1].split(' ')[0]
        val =  ureg(val).m_as(ureg.uM)
        vals.append(val)
    except:
        pass

    try:
        q = re.split('[=~<>]',str(lit))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(lit))[1].split(' ')[0]
        val =  ureg(val).m_as(1/ureg.uM)
        vals.append(1/val)
    except:
        pass

    try:
        q = re.split('[=~<>]',str(moad))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(moad))[1].split(' ')[0]
        val = ureg(val).m_as(ureg.uM)
        vals.append(val)
    except:
        pass

    try:
        q = re.split('[=~<>]',str(moad))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(moad))[1].split(' ')[0]
        val = ureg(val).m_as(1/ureg.uM)
        vals.append(1/moad)
    except:
        pass

    try:
        q = re.split('[=~<>]',str(pdbbind))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(pdbbind))[1].split(' ')[0]
        val = ureg(val).m_as(ureg.uM)
        vals.append(val)
    except:
        pass

    try:
        q = re.split('[=~<>]',str(pdbbind))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(pdbbind))[1].split(' ')[0]
        val = ureg(val).m_as(1/ureg.uM)
        vals.append(1/val)
    except:
        pass

    try:
        q = re.split('[=~<>]',str(bindingdb))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(bindingdb))[1].split(' ')[0]
        val =  ureg(val).m_as(ureg.uM)
        vals.append(val)
    except:
        pass

    try:
        q = re.split('[=~<>]',str(bindingdb))[0].lower()
        if q not in quantities:
            others.add(q)
            raise
        val = re.split('[=~<>]',str(bindingdb))[1].split(' ')[0]
        val =  ureg(val).m_as(1/ureg.uM)
        vals.append(1/val)
    except:
        pass

    if len(vals) > 0:
        vals = np.array(vals)
        return np.mean(vals[~np.isnan(vals)])
    
    return None

In [58]:
df_affinity.columns

Index(['pdb', 'chain', 'l_id', 'l_chain', 'affinity_lit', 'affinity_moad',
       'affinity_pdbbind-cn', 'affinity_bindingdb', 'seq', 'ligand_fn',
       'smiles', 'affinity_uM'],
      dtype='object')

In [59]:
df_affinity['affinity_uM'] = df_affinity[['affinity_lit','affinity_moad','affinity_pdbbind-cn','affinity_bindingdb']].apply(to_uM,axis=1)

In [60]:
others

{'deltag', 'deltah', 'none'}

In [61]:
df_affinity[~df_affinity['affinity_uM'].isnull()]

pdb chain l_id  l_chain affinity_lit       affinity_moad  \
38      11gs   EAA    A        1         None  ki=1.5uM (GTT EAA)   
43      13gs   SAS    A        1         None       ki=24uM (SAS)   
53      16pk   BIS    A        1         None                None   
54      17gs   GTX    A        1         None                None   
55      181l   BNZ    A        1         None   Ka=5700M^-1 (BNZ)   
...      ...   ...  ...      ...          ...                 ...   
105118  9hvp   0E9    A        1         None                None   
105119  9hvp   0E9    A        1         None                None   
105124  9icd   NAP    A        1         None      kd=125uM (NAP)   
105133  9lpr   III    P        1         None                None   
105138  9nse   ISU    B        2         None    Ki=0.039uM (ISU)   

       affinity_pdbbind-cn affinity_bindingdb  \
38      Ki=1.5uM (GTT-EAA)               None   
43           Ki=24uM (SAS)               None   
53            Ki=6uM (BIS)               None   
54                    None         Kd=10000nM   
55                    None        Kd=175000nM   
...                    ...                ...   
105118    Ki=4.5nM (5-mer)               None   
105119    Ki=4.5nM (5-mer)               None   
105124      Kd=125uM (NAP)               None   
105133   Ki=2000nM (4-mer)               None   
105138                None               None   

                                                      seq  \
38      PYTVVYFPVRGRCAALRMLLADQGQSWKEEVVTVETWQEGSLKASC...   
43      MPPYTVVYFPVRGRCAALRMLLADQGQSWKEEVVTVETWQEGSLKA...   
53      EKKSINECDLKGKKVLIRVDFNVPVKNGKITNDYRIRSALPTLKKV...   
54      MPPYTVVYFPVRGRCAALRMLLADQGQSWKEEVVTVETWQEGSLKA...   
55      MNIFEMLRIDEGLRLKIYKDTEGYYTIGIGHLLTKSPSLNAAKSEL...   
...                                                   ...   
105118  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMNLPGRWKPKM...   
105119  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMNLPGRWKPKM...   
105124  SKVVVPAQGKKITLQNGKLNVPENPIIPYIEGDGIGVDVTPAMLKV...   
105133  ANIVGGIEYSINNASLCSVGFSVTRGATKGFVTAGHCGTVNATARI...   
105138  KFPRVKNWELGSITYDTLCAQSQQDGPCTPRRCLGSLVLPRKLQTR...   

                                  ligand_fn  \
38      biolip/data/ligand/11gs_EAA_A_1.pdb   
43      biolip/data/ligand/13gs_SAS_A_1.pdb   
53      biolip/data/ligand/16pk_BIS_A_1.pdb   
54      biolip/data/ligand/17gs_GTX_A_1.pdb   
55      biolip/data/ligand/181l_BNZ_A_1.pdb   
...                                     ...   
105118  biolip/data/ligand/9hvp_0E9_A_1.pdb   
105119  biolip/data/ligand/9hvp_0E9_A_1.pdb   
105124  biolip/data/ligand/9icd_NAP_A_1.pdb   
105133  biolip/data/ligand/9lpr_III_P_1.pdb   
105138  biolip/data/ligand/9nse_ISU_B_2.pdb   

                                                   smiles  affinity_uM  
38                CC[C@H](C(=O)c1ccc(c(c1Cl)Cl)OCC(=O)O)C       1.5000  
43      OC(=O)c1cc(/N=N/c2ccc(cc2)S(=O)(=O)Nc2ccccn2)c...      24.0000  
53      O[C@@H]1[C@@H](CO[P@](=O)(O[P@@](=O)(C(CCCC(P(...       6.0000  
54      CCCCCCSC[C@@H](C(=O)NCC(=O)O)NC(=O)CC[C@@H](C(...      10.0000  
55                                               c1ccccc1     175.0000  
...                                                   ...          ...  
105118  O[C@@H]([C@H](Cc1ccccc1)NC(=O)[C@H](C(C)C)NC(=...       0.0045  
105119  O[C@@H]([C@H](Cc1ccccc1)NC(=O)[C@H](C(C)C)NC(=...       0.0045  
105124  O[C@@H]1[C@@H](COP(=O)(O)O)O[C@H]([C@@H]1OP(=O...     125.0000  
105133  CC(C[C@@H](B(O)O)NC(=O)[C@@H]1CCCN1C(=O)[C@@H]...       2.0000  
105138                                       CC[Se]C(=N)N       0.0390  

[12851 rows x 12 columns]

In [63]:
df_affinity.to_parquet('data/biolip.parquet')

In [64]:
len(df_affinity)

13645